# kMeans in DataBricks
## First, a test with example code
using procedure from here: https://stackoverflow.com/questions/47585723/kmeans-clustering-in-pyspark  
note also DataBricks ml-docs at http://spark.apache.org/docs/latest/api/python/pyspark.ml.html#pyspark.ml.clustering.KMeans

In [0]:
df = spark.createDataFrame([[0, 33.3, -17.5],
                            [1, 40.4, -20.5],
                            [2, 28.0, -23.9],
                            [3, 29.5, -19.0],
                            [4, 32.8, -18.8]
                           ], ['other', 'lat', 'long'])
df.show()

+-----+----+-----+
other| lat| long|
+-----+----+-----+
 0|33.3|-17.5|
 1|40.4|-20.5|
 2|28.0|-23.9|
 3|29.5|-19.0|
 4|32.8|-18.8|
+-----+----+-----+

In [0]:
from pyspark.ml.feature import VectorAssembler

new_df = VectorAssembler(inputCols=['lat', 'long'], outputCol='features').transform(df)
new_df.display()

other lat long features 0 33.3 -17.5 List(1, 2, List(), List(33.3, -17.5)) 1 40.4 -20.5 List(1, 2, List(), List(40.4, -20.5)) 2 28.0 -23.9 List(1, 2, List(), List(28.0, -23.9)) 3 29.5 -19.0 List(1, 2, List(), List(29.5, -19.0)) 4 32.8 -18.8 List(1, 2, List(), List(32.8, -18.8))

In [0]:
from pyspark.ml.clustering import KMeans

# Note we say how many clusters we want here: k=2
model = KMeans(k=2, seed=1).fit(new_df)

In [0]:
transformed = model.transform(new_df)
transformed.display()

other lat long features prediction 0 33.3 -17.5 List(1, 2, List(), List(33.3, -17.5)) 0 1 40.4 -20.5 List(1, 2, List(), List(40.4, -20.5)) 0 2 28.0 -23.9 List(1, 2, List(), List(28.0, -23.9)) 1 3 29.5 -19.0 List(1, 2, List(), List(29.5, -19.0)) 1 4 32.8 -18.8 List(1, 2, List(), List(32.8, -18.8)) 0

## Now with our data!

In [0]:
# Load data from our AWS RDS database

for line in map(lambda line: line.split('=', 2), sc.textFile('/FileStore/rds.txt').collect()):
  (len(line) > 1) and globals().update({line[0]: line[1]})

df_joined = spark.read.jdbc(table='joined',
  url=f'jdbc:mysql://{rds_host}/{rds_db}?user={rds_user}&password={rds_pwd}')

print(end=f'\nLoaded df_joined ({df_joined.count():,} rows): '); df_joined.printSchema()

Loaded df_joined (15,626 rows): root
-- track_id: string (nullable = true)
-- artist_name: string (nullable = true)
-- track_name: string (nullable = true)
-- popularity: integer (nullable = true)
-- danceability: double (nullable = true)
-- energy: double (nullable = true)
-- key: integer (nullable = true)
-- loudness: double (nullable = true)
-- mode: integer (nullable = true)
-- speechiness: double (nullable = true)
-- acousticness: double (nullable = true)
-- instrumentalness: double (nullable = true)
-- liveness: double (nullable = true)
-- valence: double (nullable = true)
-- tempo: double (nullable = true)
-- duration_ms: integer (nullable = true)
-- time_signature: integer (nullable = true)

In [0]:
# Show me some data just for info

df_joined.display()

track_id artist_name track_name popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature 2b8fOow8UzyDFAE27YhOZM Maroon 5 Memories 100 0.764 0.32 11 -7.209 1 0.0546 0.8370000000000001 0.0 0.0822 0.575 91.01899999999999 189486 4 21jGcNKet2qwijlDFuPiPb Post Malone Circles 99 0.695 0.762 0 -3.497 1 0.0395 0.192 0.00244 0.0863 0.5529999999999999 120.042 215280 4 3eekarcy7kvN4yt5ZFzltW Travis Scott HIGHEST IN THE ROOM 98 0.598 0.42700000000000005 7 -8.764 0 0.0317 0.0546 5.83E-6 0.21 0.0605 76.469 175721 4 3ZCTVFBt2Brf31RLEnCkWJ Billie Eilish everything i wanted 98 0.7040000000000001 0.225 6 -14.454 0 0.0994 0.902 0.657 0.106 0.243 120.006 245426 4 2XU0oxnq2qxCpomAAuJY8K Tones and I Dance Monkey 98 0.8240000000000001 0.588 6 -6.4 0 0.0924 0.6920000000000001 1.0400000000000001E-4 0.149 0.513 98.027 209438 4 1HfMVBKM75vxSfsQ5VefZ5 Selena Gomez Lose You To Love Me 98 0.505 0.34 4 -9.005 1 0.0438 0.5760000000000001 0.0 0.21 0.0916 101.993 206459 4 7aiClxsDWFRQ0Kzk5KI5ku blackbear hot girl bummer 97 0.778 0.5589999999999999 6 -7.109 0 0.0776 0.128 0.0 0.39899999999999997 0.6779999999999999 129.989 185093 1 6cy3ki60hLwimwIje7tALf The Black Eyed Peas RITMO (Bad Boys For Life) 97 0.721 0.716 10 -7.037000000000001 0 0.0657 0.0334 8.4E-4 0.237 0.667 104.994 221714 4 6WrI0LAC5M1Rw2MnX2ZvEg Dua Lipa Don't Start Now 97 0.794 0.7929999999999999 11 -4.521 0 0.0842 0.0125 0.0 0.0952 0.677 123.941 183290 4 696DnlkuDOXcMAnKlTgXXK Arizona Zervas ROXANNE 97 0.621 0.601 6 -5.6160000000000005 0 0.14800000000000002 0.0522 0.0 0.46 0.457 116.735 163636 5 7qEHsqek33rTcFNT9PFqLf Lewis Capaldi Someone You Loved 96 0.501 0.405 1 -5.678999999999999 1 0.0319 0.7509999999999999 0.0 0.105 0.446 109.891 182161 4 2Fxmhks0bxGSBdJ92vM42m Billie Eilish bad guy 96 0.701 0.425 7 -10.965 1 0.375 0.32799999999999996 0.13 0.1 0.562 135.128 194088 4 0TK2YIli7K1leLovkQiNik Shawn Mendes Señorita 96 0.759 0.54 9 -6.039 0 0.0287 0.037000000000000005 0.0 0.0945 0.75 116.947 190960 4 5yY9lUy8nbvjM1Uyo1Uqoc Future Life Is Good (feat. Drake) 95 0.6759999999999999 0.609 2 -5.831 0 0.48100000000000004 0.0706 0.0 0.152 0.508 142.037 237735 4 2wrJq5XKLnmhRXHIAf9xBa Dan + Shay 10,000 Hours (with Justin Bieber) 95 0.654 0.63 10 -4.644 1 0.0259 0.153 0.0 0.111 0.43 89.991 167693 4 2tnVG71enUj33Ic2nFN6kZ Regard Ride It 95 0.882 0.78 0 -4.256 1 0.0939 0.159 5.22E-5 0.0973 0.867 117.945 157606 4 2ksOAxtIxY8yElEWw8RhgK Anuel AA China 95 0.7859999999999999 0.8079999999999999 7 -3.702 1 0.0882 0.0846 2.8900000000000003E-4 0.0822 0.609 105.027 301714 4 7k4t7uLgtOxPwTpFmtJNTY KAROL G Tusa 94 0.8029999999999999 0.715 2 -3.28 1 0.298 0.295 1.34E-4 0.0574 0.574 101.085 200960 4 7FIWs0pqAYbP91WWM0vlTQ Eminem Godzilla (feat. Juice WRLD) 94 0.8079999999999999 0.745 10 -5.26 0 0.342 0.145 0.0 0.292 0.8290000000000001 165.995 210800 4 6b2RcmUt1g9N9mQ3CbjX2Y Sam Smith How Do You Sleep? 94 0.47700000000000004 0.682 1 -4.931 0 0.0925 0.153 0.0 0.0763 0.345 110.56700000000001 202205 5 51Fjme0JiitpyXKuyQiCDo Y2K Lalala 94 0.843 0.391 2 -7.899 1 0.0845 0.18100000000000002 0.0 0.13699999999999998 0.496 129.972 160627 4 7LzouaWGFCy4tkXDOOnEyM Camila Cabello Liar 93 0.74 0.498 11 -6.684 0 0.0456 0.0169 0.00282 0.319 0.652 98.016 207039 4 73SpzrcaHk0RQPFP73vqVR Billie Eilish No Time To Die 93 0.38 0.21899999999999997 4 -13.273 0 0.0358 0.917 0.0104 0.0827 0.0517 73.53699999999999 242265 4 6mAN61JH0dzyZpWslS11jy Rauw Alejandro Fantasias 93 0.879 0.703 1 -4.218999999999999 1 0.0701 0.14300000000000002 0.0 0.0569 0.7879999999999999 94.00399999999999 199711 4 6Gg1gjgKi2AK4e0qzsR7sd Juice WRLD Bandit (with YoungBoy Never Broke Again) 93 0.474 0.631 5 -5.8839999999999995 0 0.34299999999999997 0.0687 0.0 0.132 0.425 180.051 189323 4 57vxBYXtHMk6H1aD29V7PU The Weeknd Heartless 93 0.531 0.75 10 -5.831 0 0.111 0.00632 7.6E-5 0.11699999999999999 0.198 169.954 200080 4 4vUmTMuQqjdnvlZmAH61Qk Ed Sheeran South of the Border (feat. Camila Cabello 

In [0]:
# And some statistics?

df_joined.summary().toPandas().set_index('summary').rename_axis('column').T.astype({'count':int})

column 
 count 
 mean 
 stddev 
 min 
 25% 
 50% 
 75% 
 max 
 
 
 
 
 track_id 
 15626 
 None 
 None 
 001UkMQHw4zXfFNdKpwXAF 
 None 
 None 
 None 
 7zzm71Fx6YaLDv6zkEBP6S 
 
 
 artist_name 
 15626 
 2371.923076923077 
 1251.4178932673703 
 $NOT 
 3030.0 
 3030.0 
 3030.0 
 須田景凪 
 
 
 track_name 
 15626 
 Infinity 
 NaN 
 ! 
 21.0 
 239.0 
 1997.0 
 달라달라 (DALLA DALLA) 
 
 
 popularity 
 15626 
 49.09823371304237 
 24.273115612133985 
 0 
 43 
 58 
 65 
 100 
 
 
 danceability 
 15626 
 0.5945621720209918 
 0.1959560776402525 
 0.0 
 0.45799999999999996 
 0.622 
 0.745 
 0.983 
 
 
 energy 
 15626 
 0.5345365907461905 
 0.27194889527461247 
 2.02E-5 
 0.337 
 0.588 
 0.75 
 1.0 
 
 
 key 
 15626 
 5.183348265710994 
 3.59410813165091 
 0 
 2 
 5 
 8 
 11 
 
 
 loudness 
 15626 
 -10.063024638423146 
 7.372410034467787 
 -45.136 
 -11.838 
 -7.166 
 -5.222 
 2.036 
 
 
 mode 
 15626 
 0.6332394726737489 
 0.4819357911020608 
 0 
 0 
 1 
 1 
 1 
 
 
 speechiness 
 15626 
 0.10978706642774833 
 0.11828840200016223 
 0.0 
 0.0399 
 0.0562 
 0.125 
 0.951 
 
 
 acousticness 
 15626 
 0.417139264029178 
 0.36293774776034904 
 0.0 
 0.0741 
 0.309 
 0.7829999999999999 
 0.996 
 
 
 instrumentalness 
 15626 
 0.16717817551900696 
 0.33367272730479636 
 0.0 
 0.0 
 3.4E-6 
 0.013999999999999999 
 0.998 
 
 
 liveness 
 15626 
 0.2003735184948166 
 0.18483663534387584 
 0.0 
 0.0976 
 0.12300000000000001 
 0.22699999999999998 
 1.0 
 
 
 valence 
 15626 
 0.4753970952259088 
 0.2506118618073717 
 0.0 
 0.27399999999999997 
 0.47 
 0.6709999999999999 
 0.9890000000000001 
 
 
 tempo 
 15626 
 119.82320587482393 
 30.937673067231266 
 0.0 
 95.015 
 120.13600000000001 
 140.03 
 235.998 
 
 
 duration_ms 
 15626 
 204291.7072827339 
 96346.33296960081 
 12564 
 160105 
 191787 
 226000 
 1493227 
 
 
 time_signature 
 15626 
 3.8844233969025983 
 0.502236193346906 
 0 
 4 
 4 
 4 
 5

In [0]:
# Assemble a list of feature columns

feature_columns = [_ for _ in df_joined.columns if _ not in ['track_id', 'artist_name', 'track_name']]

print(feature_columns)

['popularity', 'danceability', 'energy', 'key', 'loudness', 'mode', 'speechiness', 'acousticness', 'instrumentalness', 'liveness', 'valence', 'tempo', 'duration_ms', 'time_signature']

In [0]:
# Compute the vector column need for pySpark-kMeans

from pyspark.ml.feature import VectorAssembler
if ('features' in df_joined.columns): df_joined = df_joined.drop('features')

df_joined = VectorAssembler(inputCols=feature_columns, outputCol='features').transform(df_joined)

df_joined.display()

track_id artist_name track_name popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature features 2b8fOow8UzyDFAE27YhOZM Maroon 5 Memories 100 0.764 0.32 11 -7.209 1 0.0546 0.8370000000000001 0.0 0.0822 0.575 91.01899999999999 189486 4 List(1, 14, List(), List(100.0, 0.764, 0.32, 11.0, -7.209, 1.0, 0.0546, 0.8370000000000001, 0.0, 0.0822, 0.575, 91.01899999999999, 189486.0, 4.0)) 21jGcNKet2qwijlDFuPiPb Post Malone Circles 99 0.695 0.762 0 -3.497 1 0.0395 0.192 0.00244 0.0863 0.5529999999999999 120.042 215280 4 List(1, 14, List(), List(99.0, 0.695, 0.762, 0.0, -3.497, 1.0, 0.0395, 0.192, 0.00244, 0.0863, 0.5529999999999999, 120.042, 215280.0, 4.0)) 3eekarcy7kvN4yt5ZFzltW Travis Scott HIGHEST IN THE ROOM 98 0.598 0.42700000000000005 7 -8.764 0 0.0317 0.0546 5.83E-6 0.21 0.0605 76.469 175721 4 List(1, 14, List(), List(98.0, 0.598, 0.42700000000000005, 7.0, -8.764, 0.0, 0.0317, 0.0546, 5.83E-6, 0.21, 0.0605, 76.469, 175721.0, 4.0)) 3ZCTVFBt2Brf31RLEnCkWJ Billie Eilish everything i wanted 98 0.7040000000000001 0.225 6 -14.454 0 0.0994 0.902 0.657 0.106 0.243 120.006 245426 4 List(1, 14, List(), List(98.0, 0.7040000000000001, 0.225, 6.0, -14.454, 0.0, 0.0994, 0.902, 0.657, 0.106, 0.243, 120.006, 245426.0, 4.0)) 2XU0oxnq2qxCpomAAuJY8K Tones and I Dance Monkey 98 0.8240000000000001 0.588 6 -6.4 0 0.0924 0.6920000000000001 1.0400000000000001E-4 0.149 0.513 98.027 209438 4 List(1, 14, List(), List(98.0, 0.8240000000000001, 0.588, 6.0, -6.4, 0.0, 0.0924, 0.6920000000000001, 1.0400000000000001E-4, 0.149, 0.513, 98.027, 209438.0, 4.0)) 1HfMVBKM75vxSfsQ5VefZ5 Selena Gomez Lose You To Love Me 98 0.505 0.34 4 -9.005 1 0.0438 0.5760000000000001 0.0 0.21 0.0916 101.993 206459 4 List(1, 14, List(), List(98.0, 0.505, 0.34, 4.0, -9.005, 1.0, 0.0438, 0.5760000000000001, 0.0, 0.21, 0.0916, 101.993, 206459.0, 4.0)) 7aiClxsDWFRQ0Kzk5KI5ku blackbear hot girl bummer 97 0.778 0.5589999999999999 6 -7.109 0 0.0776 0.128 0.0 0.39899999999999997 0.6779999999999999 129.989 185093 1 List(1, 14, List(), List(97.0, 0.778, 0.5589999999999999, 6.0, -7.109, 0.0, 0.0776, 0.128, 0.0, 0.39899999999999997, 0.6779999999999999, 129.989, 185093.0, 1.0)) 6cy3ki60hLwimwIje7tALf The Black Eyed Peas RITMO (Bad Boys For Life) 97 0.721 0.716 10 -7.037000000000001 0 0.0657 0.0334 8.4E-4 0.237 0.667 104.994 221714 4 List(1, 14, List(), List(97.0, 0.721, 0.716, 10.0, -7.037000000000001, 0.0, 0.0657, 0.0334, 8.4E-4, 0.237, 0.667, 104.994, 221714.0, 4.0)) 6WrI0LAC5M1Rw2MnX2ZvEg Dua Lipa Don't Start Now 97 0.794 0.7929999999999999 11 -4.521 0 0.0842 0.0125 0.0 0.0952 0.677 123.941 183290 4 List(1, 14, List(), List(97.0, 0.794, 0.7929999999999999, 11.0, -4.521, 0.0, 0.0842, 0.0125, 0.0, 0.0952, 0.677, 123.941, 183290.0, 4.0)) 696DnlkuDOXcMAnKlTgXXK Arizona Zervas ROXANNE 97 0.621 0.601 6 -5.6160000000000005 0 0.14800000000000002 0.0522 0.0 0.46 0.457 116.735 163636 5 List(1, 14, List(), List(97.0, 0.621, 0.601, 6.0, -5.6160000000000005, 0.0, 0.14800000000000002, 0.0522, 0.0, 0.46, 0.457, 116.735, 163636.0, 5.0)) 7qEHsqek33rTcFNT9PFqLf Lewis Capaldi Someone You Loved 96 0.501 0.405 1 -5.678999999999999 1 0.0319 0.7509999999999999 0.0 0.105 0.446 109.891 182161 4 List(1, 14, List(), List(96.0, 0.501, 0.405, 1.0, -5.678999999999999, 1.0, 0.0319, 0.7509999999999999, 0.0, 0.105, 0.446, 109.891, 182161.0, 4.0)) 2Fxmhks0bxGSBdJ92vM42m Billie Eilish bad guy 96 0.701 0.425 7 -10.965 1 0.375 0.32799999999999996 0.13 0.1 0.562 135.128 194088 4 List(1, 14, List(), List(96.0, 0.701, 0.425, 7.0, -10.965, 1.0, 0.375, 0.32799999999999996, 0.13, 0.1, 0.562, 135.128, 194088.0, 4.0)) 0TK2YIli7K1leLovkQiNik Shawn Mendes Señorita 96 0.759 0.54 9 -6.039 0 0.0287 0.037000000000000005 0.0 0.0945 0.75 116.947 190960 4 List(1, 14, List(), List(96.0, 0.759, 0.54, 9.0, -6.039, 0.0, 0.0287, 0.037000000000000005, 0.0, 0.0945, 0.75, 116.947, 190960.0, 4.0)) 5yY9lUy8nbvjM1Uyo1Uqoc Future Life Is Good (feat. Drake) 95 0.67599999999999

In [0]:
# Scale the features to value range 0..1

from pyspark.ml.feature import MinMaxScaler
if ('scaledFeatures' in df_joined.columns): df_joined = df_joined.drop('scaledFeatures')

df_joined = MinMaxScaler(inputCol='features', outputCol='scaledFeatures') \
  .fit(df_joined).transform(df_joined)

df_joined.display()

track_id artist_name track_name popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature features scaledFeatures 2b8fOow8UzyDFAE27YhOZM Maroon 5 Memories 100 0.764 0.32 11 -7.209 1 0.0546 0.8370000000000001 0.0 0.0822 0.575 91.01899999999999 189486 4 List(1, 14, List(), List(100.0, 0.764, 0.32, 11.0, -7.209, 1.0, 0.0546, 0.8370000000000001, 0.0, 0.0822, 0.575, 91.01899999999999, 189486.0, 4.0)) List(1, 14, List(), List(1.0, 0.7772126144455749, 0.3199862637225272, 1.0, 0.8040150936996524, 1.0, 0.057413249211356474, 0.8403614457831327, 0.0, 0.0822, 0.5813953488372091, 0.3856769972626886, 0.11948836433408548, 0.8)) 21jGcNKet2qwijlDFuPiPb Post Malone Circles 99 0.695 0.762 0 -3.497 1 0.0395 0.192 0.00244 0.0863 0.5529999999999999 120.042 215280 4 List(1, 14, List(), List(99.0, 0.695, 0.762, 0.0, -3.497, 1.0, 0.0395, 0.192, 0.00244, 0.0863, 0.5529999999999999, 120.042, 215280.0, 4.0)) List(1, 14, List(), List(0.99, 0.7070193285859614, 0.7619951923028845, 0.0, 0.8827058424489104, 1.0, 0.041535226077812834, 0.1927710843373494, 0.0024448897795591178, 0.0863, 0.5591506572295246, 0.5086568530241782, 0.13690893876594473, 0.8)) 3eekarcy7kvN4yt5ZFzltW Travis Scott HIGHEST IN THE ROOM 98 0.598 0.42700000000000005 7 -8.764 0 0.0317 0.0546 5.83E-6 0.21 0.0605 76.469 175721 4 List(1, 14, List(), List(98.0, 0.598, 0.42700000000000005, 7.0, -8.764, 0.0, 0.0317, 0.0546, 5.83E-6, 0.21, 0.0605, 76.469, 175721.0, 4.0)) List(1, 14, List(), List(0.98, 0.6083418107833164, 0.4269884251661884, 0.6363636363636364, 0.7710506232510811, 0.0, 0.03333333333333333, 0.05481927710843374, 5.8416833667334665E-6, 0.21, 0.06117290192113244, 0.3240239324062068, 0.11019185324412105, 0.8)) 3ZCTVFBt2Brf31RLEnCkWJ Billie Eilish everything i wanted 98 0.7040000000000001 0.225 6 -14.454 0 0.0994 0.902 0.657 0.106 0.243 120.006 245426 4 List(1, 14, List(), List(98.0, 0.7040000000000001, 0.225, 6.0, -14.454, 0.0, 0.0994, 0.902, 0.657, 0.106, 0.243, 120.006, 245426.0, 4.0)) List(1, 14, List(), List(0.98, 0.7161749745676502, 0.22498434468376263, 0.5454545454545454, 0.650428220130586, 0.0, 0.10452155625657204, 0.9056224899598394, 0.658316633266533, 0.106, 0.24570273003033363, 0.5085043093585538, 0.1572687370454992, 0.8)) 2XU0oxnq2qxCpomAAuJY8K Tones and I Dance Monkey 98 0.8240000000000001 0.588 6 -6.4 0 0.0924 0.6920000000000001 1.0400000000000001E-4 0.149 0.513 98.027 209438 4 List(1, 14, List(), List(98.0, 0.8240000000000001, 0.588, 6.0, -6.4, 0.0, 0.0924, 0.6920000000000001, 1.0400000000000001E-4, 0.149, 0.513, 98.027, 209438.0, 4.0)) List(1, 14, List(), List(0.98, 0.8382502543234996, 0.5879916774318841, 0.5454545454545454, 0.8211650979394557, 0.0, 0.0971608832807571, 0.6947791164658635, 1.0420841683366733E-4, 0.149, 0.518705763397371, 0.4153721641708828, 0.13296340895936484, 0.8)) 1HfMVBKM75vxSfsQ5VefZ5 Selena Gomez Lose You To Love Me 98 0.505 0.34 4 -9.005 1 0.0438 0.5760000000000001 0.0 0.21 0.0916 101.993 206459 4 List(1, 14, List(), List(98.0, 0.505, 0.34, 4.0, -9.005, 1.0, 0.0438, 0.5760000000000001, 0.0, 0.21, 0.0916, 101.993, 206459.0, 4.0)) List(1, 14, List(), List(0.98, 0.5137334689725331, 0.3399866677306882, 0.36363636363636365, 0.7659416603069618, 1.0, 0.046056782334384865, 0.5783132530120483, 0.0, 0.21, 0.09261880687563194, 0.4321773913338248, 0.13095147241472233, 0.8)) 7aiClxsDWFRQ0Kzk5KI5ku blackbear hot girl bummer 97 0.778 0.5589999999999999 6 -7.109 0 0.0776 0.128 0.0 0.39899999999999997 0.6779999999999999 129.989 185093 1 List(1, 14, List(), List(97.0, 0.778, 0.5589999999999999, 6.0, -7.109, 0.0, 0.0776, 0.128, 0.0, 0.39899999999999997, 0.6779999999999999, 129.989, 185093.0, 1.0)) List(1, 14, List(), List(0.97, 0.7914547304170906, 0.5589910916200507, 0.5454545454545454, 0.8061349953362164, 0.0, 0.08159831756046268, 0.12851405622489961, 0.0, 0.39899999999999997, 0.6855409504550048, 0.5508055153009771, 0.11652145018819272, 0.2)) 6cy3ki60hLwimwIje7tALf The Black Eyed Peas RIT

In [0]:
# Perform a principal component analysis
# Note: Actually, with only 14 features, we opted to skip this step 

# from pyspark.ml.feature import PCA
# if ('pcaFeatures' in df_joined.columns): df_joined = df_joined.drop('pcaFeatures')
#
# import pandas as pd
# pd.DataFrame([sum(map(abs, _)) for _ in PCA(k=3, inputCol='scaledFeatures').fit(df_joined).pc.toArray()],
#   index=feature_columns).sort_values(0, ascending=False).rename(columns={0: 'PCA feature importance'})
#
# df_joined = PCA(k=10, inputCol='scaledFeatures', outputCol='pcaFeatures').fit(df_joined).transform(df_joined)
#
# df_joined.display()

In [0]:
# Initialize the kMeans model

from pyspark.ml.clustering import KMeans

model = KMeans(k=50, seed=42, featuresCol='features').fit(df_joined)

print(model, *model.extractParamMap().items(), sep='\n')

KMeansModel: uid=KMeans_784a545ef8eb, k=50, distanceMeasure=euclidean, numFeatures=14
(Param(parent='KMeans_784a545ef8eb', name='distanceMeasure', doc="the distance measure. Supported options: 'euclidean' and 'cosine'."), 'euclidean')
(Param(parent='KMeans_784a545ef8eb', name='featuresCol', doc='features column name.'), 'features')
(Param(parent='KMeans_784a545ef8eb', name='initMode', doc='The initialization algorithm. This can be either "random" to choose random points as initial cluster centers, or "k-means||" to use a parallel variant of k-means++'), 'k-means||')
(Param(parent='KMeans_784a545ef8eb', name='initSteps', doc='The number of steps for k-means|| initialization mode. Must be > 0.'), 2)
(Param(parent='KMeans_784a545ef8eb', name='k', doc='The number of clusters to create. Must be > 1.'), 50)
(Param(parent='KMeans_784a545ef8eb', name='maxIter', doc='max number of iterations (>= 0).'), 20)
(Param(parent='KMeans_784a545ef8eb', name='predictionCol', doc='prediction column name.'), 'prediction')
(Param(parent='KMeans_784a545ef8eb', name='seed', doc='random seed.'), 42)
(Param(parent='KMeans_784a545ef8eb', name='tol', doc='the convergence tolerance for iterative algorithms (>= 0).'), 0.0001)

In [0]:
# Where are our cluster centers located?
# (These can be intepreted as something like feature-weights)

feature_weights = spark.createDataFrame(schema=['cluster', *feature_columns],
  data=[[i] + _.tolist() for i, _ in enumerate(model.clusterCenters())])

feature_weights.display()

cluster popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature 0 51.019067796610166 0.6334671610169491 0.5174297796610172 5.271186440677966 -10.6143093220339 0.6165254237288136 0.1321875 0.4351521237288135 0.20961467150423732 0.17161440677966086 0.5195756779661019 123.90557838983052 139984.13983050847 3.836864406779661 1 13.40909090909091 0.3096909090909092 0.19980681818181817 5.7272727272727275 -19.475409090909086 0.6363636363636364 0.044559090909090916 0.8272969545454546 0.6207977272727272 0.1688909090909091 0.18901818181818184 114.45718181818182 657678.9545454546 3.772727272727273 2 12.788732394366198 0.44074647887323926 0.19648823943661967 4.753521126760564 -23.08083802816901 0.795774647887324 0.1049042253521127 0.8553246732394364 0.6291991362676059 0.18767112676056333 0.5233330985915498 113.71642253521125 47783.42957746479 3.6619718309859155 3 25.82828282828283 0.39393939393939403 0.33899121212121197 5.343434343434344 -16.088777777777775 0.7474747474747475 0.055645454545454553 0.6491069686868687 0.4017554032323232 0.21671414141414128 0.30617474747474743 117.67563636363636 410562.393939394 3.8282828282828287 4 51.089314194577355 0.5844063795853273 0.5634974641148325 5.244019138755981 -9.05039074960127 0.6395534290271132 0.0961189792663475 0.37773851279106874 0.11000663897926642 0.2113972886762358 0.4628481658692189 119.12345295055829 229426.06698564594 3.9027113237639552 5 17.113636363636363 0.35378636363636373 0.19973727272727274 5.0227272727272725 -19.307409090909097 0.5909090909090909 0.050763636363636344 0.8101688636363633 0.6050410218181818 0.15378863636363638 0.22079545454545454 107.32747727272731 561123.4090909091 3.8636363636363638 6 9.600000000000001 0.2698 0.1192 2.1 -21.7566 0.8 0.03876000000000001 0.9539 0.8008000000000002 0.11634 0.10652 109.41730000000001 1038710.9 3.8000000000000003 7 29.619909502262445 0.5335022624434392 0.31836034389140294 5.30316742081448 -16.738760180995477 0.6742081447963801 0.11884570135746615 0.68480243438914 0.43537669565610865 0.16281583710407246 0.46053212669683224 113.82868778280547 94655.37104072399 3.7511312217194575 8 33.84065934065934 0.4417505494505494 0.3883847802197801 4.653846153846154 -14.006950549450552 0.6538461538461539 0.06858021978021978 0.5939697607142859 0.32111167065934043 0.20845329670329663 0.33367692307692326 112.3703021978021 332564.96153846156 3.895604395604396 9 55.77696078431372 0.6123860294117651 0.5903690686274511 5.08578431372549 -8.235870098039213 0.6311274509803921 0.10065919117647051 0.3337077044362749 0.09752623455882349 0.19608615196078416 0.48183443627451056 119.76491789215682 213437.46078431373 3.911764705882353 10 47.69972451790634 0.6169413223140492 0.43375694297520656 4.75206611570248 -12.633404958677692 0.628099173553719 0.14776501377410464 0.5251090600550965 0.26806495537190067 0.1693763085399449 0.4848319834710747 120.32723415977972 121511.72727272728 3.878787878787879 11 48.160857908847184 0.5345099195710452 0.5331770509383382 5.13941018766756 -10.091426273458442 0.6246648793565683 0.08942091152815021 0.41594869302949067 0.16922560876675605 0.20369410187667555 0.3951790884718498 116.7648257372654 274253.3029490617 3.8659517426273458 12 55.89224137931034 0.6385823275862081 0.6272008081896552 5.21875 -7.452914870689656 0.6066810344827586 0.10648232758620682 0.30293414115301714 0.07987246155172419 0.20332564655172425 0.5093201508620684 123.53884159482766 192409.53125 3.927801724137931 13 55.829865361077104 0.6473667074663401 0.595054343941249 5.13219094247246 -8.009117503059974 0.6083231334149326 0.12505287637698895 0.32979781509179923 0.08910106818849452 0.2022301101591188 0.5115225458996329 122.50077233782116 179440.33170134638 3.932680538555691 14 31.3984375 0.39303359375000013 0.36560476562499983 5.015625 -15.885968750000002 0.765625 0.07160781249999996 0.6271337427343752 0.34377362281250007 0.23787421874999995 0.29871953124999995 113.80951562499999 38595

In [0]:
# Display those feature-weights as something like a heatmap
# (we need to normalize the weights for heatmap-display)

feature_weights = feature_weights.toPandas().set_index('cluster')

for feature in feature_columns: feature_min = feature_weights[feature].min(); \
  feature_weights[feature] = (feature_weights[feature] - feature_min) / (feature_weights[feature].max() - feature_min)

!pip install jinja2
display(feature_weights.style.background_gradient(cmap='coolwarm', vmin=0, vmax=1) \
        .format('{:.3%}').set_properties(**{'width':'111px', 'text-align':'center'}))

popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature cluster 
 
 0 
 91.060% 
 93.953% 
 78.392% 
 60.259% 
 81.424% 
 9.524% 
 55.091% 
 19.930% 
 16.805% 
 49.650% 
 86.740% 
 99.555% 
 8.072% 
 67.373% 
 
 
 1 
 23.933% 
 19.662% 
 15.867% 
 68.660% 
 29.358% 
 14.205% 
 3.636% 
 79.042% 
 67.330% 
 47.840% 
 23.913% 
 78.842% 
 43.947% 
 54.545% 
 
 
 2 
 22.826% 
 49.733% 
 15.214% 
 50.723% 
 8.173% 
 51.816% 
 39.070% 
 83.267% 
 68.363% 
 60.325% 
 87.454% 
 77.218% 
 1.683% 
 32.394% 
 
 
 3 
 46.099% 
 38.993% 
 43.266% 
 61.590% 
 49.257% 
 40.420% 
 10.146% 
 52.182% 
 40.415% 
 79.634% 
 46.180% 
 85.897% 
 26.822% 
 65.657% 
 
 
 4 
 91.185% 
 82.696% 
 87.460% 
 59.758% 
 90.614% 
 14.957% 
 33.912% 
 11.276% 
 4.565% 
 76.099% 
 75.958% 
 89.071% 
 14.270% 
 80.542% 
 
 
 5 
 30.545% 
 29.780% 
 15.854% 
 55.682% 
 30.345% 
 3.480% 
 7.279% 
 76.460% 
 65.394% 
 37.799% 
 29.953% 
 63.212% 
 37.256% 
 72.727% 
 
 
 6 
 17.134% 
 10.509% 
 0.000% 
 1.842% 
 15.954% 
 52.813% 
 0.231% 
 98.126% 
 89.449% 
 12.902% 
 8.233% 
 67.794% 
 70.351% 
 60.000% 
 
 
 7 
 52.866% 
 71.016% 
 39.205% 
 60.848% 
 45.438% 
 23.133% 
 47.257% 
 57.562% 
 44.546% 
 43.801% 
 75.518% 
 77.464% 
 4.931% 
 50.226% 
 
 
 8 
 60.399% 
 49.963% 
 52.989% 
 48.887% 
 61.490% 
 18.329% 
 17.741% 
 43.870% 
 30.505% 
 74.142% 
 51.407% 
 74.267% 
 21.417% 
 79.121% 
 
 
 9 
 99.552% 
 89.116% 
 92.750% 
 56.843% 
 95.400% 
 12.969% 
 36.578% 
 4.639% 
 3.032% 
 65.920% 
 79.567% 
 90.477% 
 13.162% 
 82.353% 
 
 
 10 
 85.135% 
 90.161% 
 61.921% 
 50.696% 
 69.560% 
 12.255% 
 64.238% 
 33.490% 
 23.987% 
 48.162% 
 80.136% 
 91.710% 
 6.792% 
 75.758% 
 
 
 11 
 85.958% 
 71.247% 
 81.491% 
 57.831% 
 84.497% 
 11.444% 
 29.979% 
 17.036% 
 11.842% 
 70.978% 
 63.097% 
 83.901% 
 17.376% 
 73.190% 
 
 
 12 
 99.758% 
 95.126% 
 100.000% 
 59.293% 
 100.000% 
 7.201% 
 39.997% 
 0.000% 
 0.862% 
 70.733% 
 84.791% 
 98.751% 
 11.705% 
 85.560% 
 
 
 13 
 99.646% 
 97.142% 
 93.672% 
 57.698% 
 96.732% 
 7.589% 
 50.901% 
 4.049% 
 1.996% 
 70.005% 
 85.209% 
 96.475% 
 10.806% 
 86.536% 
 
 
 14 
 56.041% 
 38.785% 
 48.505% 
 55.551% 
 50.449% 
 44.702% 
 19.519% 
 48.869% 
 33.290% 
 93.702% 
 44.763% 
 77.422% 
 25.117% 
 71.875% 
 
 
 15 
 95.232% 
 98.923% 
 93.742% 
 60.761% 
 94.345% 
 3.222% 
 50.252% 
 10.926% 
 3.608% 
 85.303% 
 92.114% 
 97.950% 
 9.542% 
 86.421% 
 
 
 16 
 77.836% 
 77.445% 
 48.472% 
 62.132% 
 60.203% 
 17.622% 
 63.764% 
 46.802% 
 30.143% 
 57.905% 
 74.895% 
 86.889% 
 5.936% 
 47.119% 
 
 
 17 
 6.782% 
 12.344% 
 7.272% 
 55.263% 
 28.492% 
 100.000% 
 4.412% 
 98.412% 
 65.832% 
 4.299% 
 16.155% 
 49.829% 
 100.000% 
 60.000% 
 
 
 18 
 11.984% 
 14.816% 
 0.470% 
 100.000% 
 16.181% 
 32.589% 
 76.774% 
 94.114% 
 68.294% 
 3.444% 
 10.046% 
 33.019% 
 79.860% 
 42.857% 
 
 
 19 
 14.755% 
 31.664% 
 6.966% 
 71.228% 
 17.632% 
 52.813% 
 39.123% 
 87.571% 
 87.524% 
 52.712% 
 25.176% 
 90.306% 
 56.499% 
 46.667% 
 
 
 20 
 38.525% 
 54.945% 
 30.147% 
 70.452% 
 37.059% 
 29.633% 
 37.591% 
 70.533% 
 48.373% 
 59.307% 
 79.106% 
 63.553% 
 3.745% 
 34.503% 
 
 
 21 
 41.486% 
 35.837% 
 23.902% 
 64.946% 
 28.853% 
 42.528% 
 5.146% 
 67.257% 
 57.190% 
 53.902% 
 36.782% 
 75.158% 
 30.856% 
 51.282% 
 
 
 22 
 100.000% 
 90.494% 
 93.438% 
 57.568% 
 96.004% 
 10.040% 
 38.361% 
 4.750% 
 1.582% 
 64.212% 
 79.675% 
 91.958% 
 12.652% 
 88.070% 
 
 
 23 
 5.354% 
 59.807% 
 8.435% 
 51.012% 
 0.000% 
 63.702% 
 100.000% 
 90.809% 
 60.330% 
 52.674% 
 99.369% 
 54.178% 
 0.000% 
 7.692% 
 
 
 24 
 99.145% 
 96.175% 
 97.053% 
 62.948% 
 98.653% 
 4.508% 
 40.706% 
 2.850% 
 0.000% 
 80.737% 
 86.622% 
 96.800% 
 11.238% 
 91.781% 
 
 
 25 
 98.004% 
 99.590% 
 95.153% 
 58.319% 
 94.627% 
 9.196% 
 54.529% 
 7.378% 
 5.367% 
 66.303% 
 89.411% 
 100.000% 
 9.097% 
 83.575% 
 
 
 26 
 39.428% 
 15.728% 


In [0]:
# Do the kMeans cluster prediction

model.setPredictionCol('cluster')
if ('cluster' in df_joined.columns): df_joined = df_joined.drop('cluster')

df_joined = model.transform(df_joined)

df_joined.display()

track_id artist_name track_name popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature features scaledFeatures cluster 2b8fOow8UzyDFAE27YhOZM Maroon 5 Memories 100 0.764 0.32 11 -7.209 1 0.0546 0.8370000000000001 0.0 0.0822 0.575 91.01899999999999 189486 4 List(1, 14, List(), List(100.0, 0.764, 0.32, 11.0, -7.209, 1.0, 0.0546, 0.8370000000000001, 0.0, 0.0822, 0.575, 91.01899999999999, 189486.0, 4.0)) List(1, 14, List(), List(1.0, 0.7772126144455749, 0.3199862637225272, 1.0, 0.8040150936996524, 1.0, 0.057413249211356474, 0.8403614457831327, 0.0, 0.0822, 0.5813953488372091, 0.3856769972626886, 0.11948836433408548, 0.8)) 12 21jGcNKet2qwijlDFuPiPb Post Malone Circles 99 0.695 0.762 0 -3.497 1 0.0395 0.192 0.00244 0.0863 0.5529999999999999 120.042 215280 4 List(1, 14, List(), List(99.0, 0.695, 0.762, 0.0, -3.497, 1.0, 0.0395, 0.192, 0.00244, 0.0863, 0.5529999999999999, 120.042, 215280.0, 4.0)) List(1, 14, List(), List(0.99, 0.7070193285859614, 0.7619951923028845, 0.0, 0.8827058424489104, 1.0, 0.041535226077812834, 0.1927710843373494, 0.0024448897795591178, 0.0863, 0.5591506572295246, 0.5086568530241782, 0.13690893876594473, 0.8)) 9 3eekarcy7kvN4yt5ZFzltW Travis Scott HIGHEST IN THE ROOM 98 0.598 0.42700000000000005 7 -8.764 0 0.0317 0.0546 5.83E-6 0.21 0.0605 76.469 175721 4 List(1, 14, List(), List(98.0, 0.598, 0.42700000000000005, 7.0, -8.764, 0.0, 0.0317, 0.0546, 5.83E-6, 0.21, 0.0605, 76.469, 175721.0, 4.0)) List(1, 14, List(), List(0.98, 0.6083418107833164, 0.4269884251661884, 0.6363636363636364, 0.7710506232510811, 0.0, 0.03333333333333333, 0.05481927710843374, 5.8416833667334665E-6, 0.21, 0.06117290192113244, 0.3240239324062068, 0.11019185324412105, 0.8)) 45 3ZCTVFBt2Brf31RLEnCkWJ Billie Eilish everything i wanted 98 0.7040000000000001 0.225 6 -14.454 0 0.0994 0.902 0.657 0.106 0.243 120.006 245426 4 List(1, 14, List(), List(98.0, 0.7040000000000001, 0.225, 6.0, -14.454, 0.0, 0.0994, 0.902, 0.657, 0.106, 0.243, 120.006, 245426.0, 4.0)) List(1, 14, List(), List(0.98, 0.7161749745676502, 0.22498434468376263, 0.5454545454545454, 0.650428220130586, 0.0, 0.10452155625657204, 0.9056224899598394, 0.658316633266533, 0.106, 0.24570273003033363, 0.5085043093585538, 0.1572687370454992, 0.8)) 28 2XU0oxnq2qxCpomAAuJY8K Tones and I Dance Monkey 98 0.8240000000000001 0.588 6 -6.4 0 0.0924 0.6920000000000001 1.0400000000000001E-4 0.149 0.513 98.027 209438 4 List(1, 14, List(), List(98.0, 0.8240000000000001, 0.588, 6.0, -6.4, 0.0, 0.0924, 0.6920000000000001, 1.0400000000000001E-4, 0.149, 0.513, 98.027, 209438.0, 4.0)) List(1, 14, List(), List(0.98, 0.8382502543234996, 0.5879916774318841, 0.5454545454545454, 0.8211650979394557, 0.0, 0.0971608832807571, 0.6947791164658635, 1.0420841683366733E-4, 0.149, 0.518705763397371, 0.4153721641708828, 0.13296340895936484, 0.8)) 22 1HfMVBKM75vxSfsQ5VefZ5 Selena Gomez Lose You To Love Me 98 0.505 0.34 4 -9.005 1 0.0438 0.5760000000000001 0.0 0.21 0.0916 101.993 206459 4 List(1, 14, List(), List(98.0, 0.505, 0.34, 4.0, -9.005, 1.0, 0.0438, 0.5760000000000001, 0.0, 0.21, 0.0916, 101.993, 206459.0, 4.0)) List(1, 14, List(), List(0.98, 0.5137334689725331, 0.3399866677306882, 0.36363636363636365, 0.7659416603069618, 1.0, 0.046056782334384865, 0.5783132530120483, 0.0, 0.21, 0.09261880687563194, 0.4321773913338248, 0.13095147241472233, 0.8)) 22 7aiClxsDWFRQ0Kzk5KI5ku blackbear hot girl bummer 97 0.778 0.5589999999999999 6 -7.109 0 0.0776 0.128 0.0 0.39899999999999997 0.6779999999999999 129.989 185093 1 List(1, 14, List(), List(97.0, 0.778, 0.5589999999999999, 6.0, -7.109, 0.0, 0.0776, 0.128, 0.0, 0.39899999999999997, 0.6779999999999999, 129.989, 185093.0, 1.0)) List(1, 14, List(), List(0.97, 0.7914547304170906, 0.5589910916200507, 0.5454545454545454, 0.8061349953362164, 0.0, 0.08159831756046268, 0.12851405622489961, 0.0, 0.39899999999999997, 0.6855409504550048, 0.5508055153009771, 0.11652145018819272, 0.2)) 24 6cy3ki60hLwimwIje7

In [0]:
# What sizes are the clusters we found?

cluster_counts = df_joined.groupBy('cluster').count()

cluster_counts.orderBy('count', ascending=False).display()

cluster count 12 927 39 884 22 857 9 818 13 816 24 803 45 730 35 723 15 708 40 701 25 626 4 625 47 601 48 555 28 476 27 473 0 468 33 385 11 373 10 358 16 294 34 289 7 221 36 208 8 183 49 183 20 171 31 147 2 142 41 138 14 128 3 99 30 84 21 78 23 52 44 51 46 51 5 44 43 29 32 25 1 22 29 20 19 15 26 11 6 10 37 8 18 7 17 5 38 3 42 1

In [0]:
# What sizes are the clusters we found? (eye-candy)

cluster_counts.orderBy('cluster').display()

cluster count 0 468 1 22 2 142 3 99 4 625 5 44 6 10 7 221 8 183 9 818 10 358 11 373 12 927 13 816 14 128 15 708 16 294 17 5 18 7 19 15 20 171 21 78 22 857 23 52 24 803 25 626 26 11 27 473 28 476 29 20 30 84 31 147 32 25 33 385 34 289 35 723 36 208 37 8 38 3 39 884 40 701 41 138 42 1 43 29 44 51 45 730 46 51 47 601 48 555 49 183

In [0]:
# Well, let's actually test our clustering. Choose a title we are coming from:

#df_joined.where("track_name like '%Rule Britannia%'").orderBy('artist_name', 'track_name').display()

source_track_id = '3OBr2Y0n4S0BWwA7SxKfwU'
source_details = df_joined.where(f"track_id == '{source_track_id}'")
source_cluster = source_details.select('cluster').head()[0]
source_details.drop(*feature_columns, 'features', 'scaledFeatures', 'pcaFeatures').display()

track_id artist_name track_name cluster 3OBr2Y0n4S0BWwA7SxKfwU Ludwig van Beethoven Beethoven: 5 Variations on "Rule Britannia" in D Major, WoO 79: Theme. Tempo moderato 2

In [0]:
# Which features are important for the cluster we are looking at?

source_top_weights = feature_weights.loc[source_cluster].nlargest(10)

print(f'Source title belongs to cluster {source_cluster}.',
      'Top weights for that cluster are:', source_top_weights, sep='\n')

Source title belongs to cluster 2.
Top weights for that cluster are:
valence 0.874539
acousticness 0.832667
tempo 0.772181
instrumentalness 0.683628
liveness 0.603255
mode 0.518156
key 0.507228
danceability 0.497327
speechiness 0.390702
time_signature 0.323944
Name: 2, dtype: float64

In [0]:
# So, what can we recommend from this cluster?

df_joined.where(f'cluster == {source_cluster}') \
  .orderBy(*source_top_weights.index, ascending=False).display()

track_id artist_name track_name popularity danceability energy key loudness mode speechiness acousticness instrumentalness liveness valence tempo duration_ms time_signature features scaledFeatures cluster 7xSZbk9JBRXkI6oHrRF0uf Johann Sebastian Bach Aria mit 30 Veränderungen, BWV 988 "Goldberg Variations": Var. 6 Canone alla Seconda a 1 Clav. 26 0.341 0.27399999999999997 7 -23.929000000000002 1 0.0475 0.9890000000000001 0.934 0.11599999999999999 0.977 117.104 50973 4 List(1, 14, List(), List(26.0, 0.341, 0.27399999999999997, 7.0, -23.929000000000002, 1.0, 0.0475, 0.9890000000000001, 0.934, 0.11599999999999999, 0.977, 117.104, 50973.0, 4.0)) List(1, 14, List(), List(0.26, 0.3468972533062055, 0.27398533450375695, 0.6363636363636364, 0.4495675400661409, 1.0, 0.04994742376445847, 0.9929718875502009, 0.9358717434869739, 0.11599999999999999, 0.9878665318503537, 0.49620759497961847, 0.025940406426040227, 0.8)) 2 0WZCZ7u8yQFNR60tyi3f5F Johann Sebastian Bach Partita n. 6 in Mi Minore: Tempo di gavotta 0 0.42100000000000004 0.483 7 -15.425999999999998 1 0.0443 0.988 0.905 0.17 0.968 120.679 50233 3 List(1, 14, List(), List(0.0, 0.42100000000000004, 0.483, 7.0, -15.425999999999998, 1.0, 0.0443, 0.988, 0.905, 0.17, 0.968, 120.679, 50233.0, 3.0)) List(1, 14, List(), List(0.0, 0.42828077314343854, 0.48298955638903907, 0.6363636363636364, 0.6298227762231833, 1.0, 0.046582544689800214, 0.9919678714859438, 0.906813627254509, 0.17, 0.9787664307381191, 0.511356028440919, 0.02544063031223175, 0.6000000000000001)) 2 5RyJw8bU1s4jHGYvRnHcdA Chris Schweizer Scorpion (ASOT 942) 38 0.6729999999999999 0.9940000000000001 1 -8.529 0 0.0596 9.259999999999999E-5 0.659 0.141 0.9640000000000001 137.858 48000 4 List(1, 14, List(), List(38.0, 0.6729999999999999, 0.9940000000000001, 1.0, -8.529, 0.0, 0.0596, 9.259999999999999E-5, 0.659, 0.141, 0.9640000000000001, 137.858, 48000.0, 4.0)) List(1, 14, List(), List(0.38, 0.6846388606307222, 0.9939998787975518, 0.09090909090909091, 0.7760323920970067, 0.0, 0.06267087276550999, 9.297188755020079E-5, 0.6603206412825651, 0.141, 0.9747219413549039, 0.5841490182120187, 0.023932522120158336, 0.8)) 2 49k3QQpaay4HrNegKre24I Ludwig van Beethoven Beethoven: 6 Variations on an Original Theme in G Major, WoO 77: Variation II 2 0.32299999999999995 0.139 7 -21.1 1 0.0395 0.988 0.8009999999999999 0.128 0.9620000000000001 75.154 51973 4 List(1, 14, List(), List(2.0, 0.32299999999999995, 0.139, 7.0, -21.1, 1.0, 0.0395, 0.988, 0.8009999999999999, 0.128, 0.9620000000000001, 75.154, 51973.0, 4.0)) List(1, 14, List(), List(0.02, 0.3285859613428281, 0.1389826074486705, 0.6363636363636364, 0.5095395573645383, 1.0, 0.041535226077812834, 0.9919678714859438, 0.8026052104208415, 0.128, 0.9726996966632961, 0.3184518512868753, 0.02661577955280844, 0.8)) 2 6DN9DnsD2Cpm3Js2GZjuGP Ludwig van Beethoven Beethoven: 7 Variations on "God Save the King" in C Major, WoO 78: Variation II 1 0.327 0.166 0 -28.857 1 0.0422 0.9890000000000001 0.773 0.139 0.961 102.219 50867 4 List(1, 14, List(), List(1.0, 0.327, 0.166, 0.0, -28.857, 1.0, 0.0422, 0.9890000000000001, 0.773, 0.139, 0.961, 102.219, 50867.0, 4.0)) List(1, 14, List(), List(0.01, 0.33265513733468977, 0.1659831528596878, 0.0, 0.34509878741626393, 1.0, 0.04437434279705574, 0.9929718875502009, 0.7745490981963927, 0.139, 0.9716885743174922, 0.4331350265680217, 0.025868816874602796, 0.8)) 2 0xmkgfnEnekpv7JBZfP65W Ludwig van Beethoven Beethoven: 7 Variations on "God Save the King" in C Major, WoO 78: Variation I 1 0.32299999999999995 0.171 0 -30.54 1 0.0662 0.996 0.871 0.153 0.96 208.959 48107 4 List(1, 14, List(), List(1.0, 0.32299999999999995, 0.171, 0.0, -30.54, 1.0, 0.0662, 0.996, 0.871, 0.153, 0.96, 208.959, 48107.0, 4.0)) List(1, 14, List(), List(0.01, 0.3285859613428281, 0.17098325386172802, 0.0, 0.3094208428728908, 1.0, 0.06961093585699264, 1.0, 0.8727454909819639, 0.153, 0.9706774519716883, 0.8854269951440267, 0.024004787044722534, 0.8)) 2 6Mm9zn5aZAq2qdVl3a6ZP7 Ludwig van Beethoven Beethoven: Pia

In [0]:
# According to our project requirement, dump the data back to our RDS instance.
# We chose to write to a separate table, creating it on the fly

!pip install pymysql sqlalchemy
from sqlalchemy import create_engine
from sqlalchemy.dialects.mysql import VARCHAR, TINYINT, MEDIUMINT

dtypes = dict(track_id=VARCHAR(25), artist_name=VARCHAR(60), track_name=VARCHAR(250))
dtypes.update({}.fromkeys([col for col, dtype in df_joined.dtypes if dtype == 'int'], TINYINT))
dtypes['duration_ms'] = MEDIUMINT

df_joined.drop('features', 'scaledFeatures', 'pcaFeatures').toPandas().set_index('track_id') \
  .to_sql(name='clustered', if_exists='replace', dtype=dtypes, method='multi',
    con=create_engine(f'mysql+pymysql://{rds_user}:{rds_pwd}@{rds_host}/{rds_db}'))